# Analysis of Neighborhoods in Toronto

## By Ben Schloss

This notebook is dedicated to the assignment for week 3 of the Applied Data Science Capstone Course, the 4th and final course in IBM's Python for Data Science Specialization. In this notebook, I first import and process data on Toronto's neighborhoods by postal code. I then use Foursquare API to retrieve information on the types of venues in each neighborhood in Old Toronto in order compile a profile on each neighborhood. Finally, I use this data to run K-means clustering on the neighborhoods in order to determine which nieghborhoods are most similar and which are most distinct.



## Note: All 3 parts of assignment are submitted within this notebook. I inserted markdown (like this) to show where the answers to each part are! Thanks!

In [603]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json
!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim

import requests
from pandas.io.json import json_normalize

!conda install -c conda-forge folium=0.5.0 --yes
import folium

from sklearn.cluster import KMeans

print('All libraries imported!')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

All libraries imported!


In [705]:
aa = pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')

In [706]:
df = pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')
df = df[0].rename(columns={'Postcode':'PostalCode', 'Neighbourhood':'Neighborhood'})
df = df.drop(df.index[df['Borough'] == 'Not assigned'])
df = df.reset_index()
df = df.drop(labels='index', axis=1)
df['Neighborhood'] = df['Neighborhood'].replace('Not assigned', df['Borough'])
df

PostalCode           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M6A        North York   
5          M7A  Downtown Toronto   
6          M9A      Queen's Park   
7          M1B       Scarborough   
8          M1B       Scarborough   
9          M3B        North York   
10         M4B         East York   
11         M4B         East York   
12         M5B  Downtown Toronto   
13         M5B  Downtown Toronto   
14         M6B        North York   
15         M9B         Etobicoke   
16         M9B         Etobicoke   
17         M9B         Etobicoke   
18         M9B         Etobicoke   
19         M9B         Etobicoke   
20         M1C       Scarborough   
21         M1C       Scarborough   
22         M1C       Scarborough   
23         M3C        North York   
24         M3C        North York   
25         M4C         East York   
26         M5C  Downtown Toronto   
27         M6C              York   
28         M9C         Etobicoke   
29         M9C         Etobicoke   
30         M9C         Etobicoke   
31         M9C         Etobicoke   
32         M1E       Scarborough   
33         M1E       Scarborough   
34         M1E       Scarborough   
35         M4E      East Toronto   
36         M5E  Downtown Toronto   
37         M6E              York   
38         M1G       Scarborough   
39         M4G         East York   
40         M5G  Downtown Toronto   
41         M6G  Downtown Toronto   
42         M1H       Scarborough   
43         M2H        North York   
44         M3H        North York   
45         M3H        North York   
46         M3H        North York   
47         M4H         East York   
48         M5H  Downtown Toronto   
49         M5H  Downtown Toronto   
50         M5H  Downtown Toronto   
51         M6H      West Toronto   
52         M6H      West Toronto   
53         M1J       Scarborough   
54         M2J        North York   
55         M2J        North York   
56         M2J        North York   
57         M3J        North York   
58         M3J        North York   
59         M4J         East York   
60         M5J  Downtown Toronto   
61         M5J  Downtown Toronto   
62         M5J  Downtown Toronto   
63         M6J      West Toronto   
64         M6J      West Toronto   
65         M1K       Scarborough   
66         M1K       Scarborough   
67         M1K       Scarborough   
68         M2K        North York   
69         M3K        North York   
70         M3K        North York   
71         M4K      East Toronto   
72         M4K      East Toronto   
73         M5K  Downtown Toronto   
74         M5K  Downtown Toronto   
75         M6K      West Toronto   
76         M6K      West Toronto   
77         M6K      West Toronto   
78         M1L       Scarborough   
79         M1L       Scarborough   
80         M1L       Scarborough   
81         M2L        North York   
82         M2L        North York   
83         M3L        North York   
84         M4L      East Toronto   
85         M4L      East Toronto   
86         M5L  Downtown Toronto   
87         M5L  Downtown Toronto   
88         M6L        North York   
89         M6L        North York   
90         M6L        North York   
91         M9L        North York   
92         M1M       Scarborough   
93         M1M       Scarborough   
94         M1M       Scarborough   
95         M2M        North York   
96         M2M        North York   
97         M3M        North York   
98         M4M      East Toronto   
99         M5M        North York   
100        M5M        North York   
101        M6M              York   
102        M6M              York   
103        M6M              York   
104        M6M              York   
105        M9M        North York   
106        M9M        North York   
107        M1N       Scarborough   
108        M1N       Scarborough   
109        M2N        North York   
110     

## FINAL TABLE FOR PART 1 BELOW:

In [707]:
df2 = df.groupby(['PostalCode', 'Borough'])['Neighborhood'].apply(list)
df2 = pd.DataFrame(data=df2)
df2['Neighborhood'] = df2['Neighborhood'].str.join(', ')
df2 = df2.reset_index()
df2

PostalCode           Borough  \
0          M1B       Scarborough   
1          M1C       Scarborough   
2          M1E       Scarborough   
3          M1G       Scarborough   
4          M1H       Scarborough   
5          M1J       Scarborough   
6          M1K       Scarborough   
7          M1L       Scarborough   
8          M1M       Scarborough   
9          M1N       Scarborough   
10         M1P       Scarborough   
11         M1R       Scarborough   
12         M1S       Scarborough   
13         M1T       Scarborough   
14         M1V       Scarborough   
15         M1W       Scarborough   
16         M1X       Scarborough   
17         M2H        North York   
18         M2J        North York   
19         M2K        North York   
20         M2L        North York   
21         M2M        North York   
22         M2N        North York   
23         M2P        North York   
24         M2R        North York   
25         M3A        North York   
26         M3B        North York   
27         M3C        North York   
28         M3H        North York   
29         M3J        North York   
30         M3K        North York   
31         M3L        North York   
32         M3M        North York   
33         M3N        North York   
34         M4A        North York   
35         M4B         East York   
36         M4C         East York   
37         M4E      East Toronto   
38         M4G         East York   
39         M4H         East York   
40         M4J         East York   
41         M4K      East Toronto   
42         M4L      East Toronto   
43         M4M      East Toronto   
44         M4N   Central Toronto   
45         M4P   Central Toronto   
46         M4R   Central Toronto   
47         M4S   Central Toronto   
48         M4T   Central Toronto   
49         M4V   Central Toronto   
50         M4W  Downtown Toronto   
51         M4X  Downtown Toronto   
52         M4Y  Downtown Toronto   
53         M5A  Downtown Toronto   
54         M5B  Downtown Toronto   
55         M5C  Downtown Toronto   
56         M5E  Downtown Toronto   
57         M5G  Downtown Toronto   
58         M5H  Downtown Toronto   
59         M5J  Downtown Toronto   
60         M5K  Downtown Toronto   
61         M5L  Downtown Toronto   
62         M5M        North York   
63         M5N   Central Toronto   
64         M5P   Central Toronto   
65         M5R   Central Toronto   
66         M5S  Downtown Toronto   
67         M5T  Downtown Toronto   
68         M5V  Downtown Toronto   
69         M5W  Downtown Toronto   
70         M5X  Downtown Toronto   
71         M6A        North York   
72         M6B        North York   
73         M6C              York   
74         M6E              York   
75         M6G  Downtown Toronto   
76         M6H      West Toronto   
77         M6J      West Toronto   
78         M6K      West Toronto   
79         M6L        North York   
80         M6M              York   
81         M6N              York   
82         M6P      West Toronto   
83         M6R      West Toronto   
84         M6S      West Toronto   
85         M7A  Downtown Toronto   
86         M7R       Mississauga   
87         M7Y      East Toronto   
88         M8V         Etobicoke   
89         M8W         Etobicoke   
90         M8X         Etobicoke   
91         M8Y         Etobicoke   
92         M8Z         Etobicoke   
93         M9A      Queen's Park   
94         M9B         Etobicoke   
95         M9C         Etobicoke   
96         M9L        North York   
97         M9M        North York   
98         M9N              York   
99         M9P         Etobicoke   
100        M9R         Etobicoke   
101        M9V         Etobicoke   
102        M9W         Etobicoke   

                                          Neighborhood  
0                                       Rouge, Malvern  
1               Highland Creek, Rouge Hill, Port Union  
2                    Guildwood, Morningside, West Hill  
3                              

## FINAL TABLE FOR PART 1 ABOVE!

In [708]:
bb = pd.read_csv('https://cocl.us/Geospatial_data')
bb

Postal Code   Latitude  Longitude
0           M1B  43.806686 -79.194353
1           M1C  43.784535 -79.160497
2           M1E  43.763573 -79.188711
3           M1G  43.770992 -79.216917
4           M1H  43.773136 -79.239476
5           M1J  43.744734 -79.239476
6           M1K  43.727929 -79.262029
7           M1L  43.711112 -79.284577
8           M1M  43.716316 -79.239476
9           M1N  43.692657 -79.264848
10          M1P  43.757410 -79.273304
11          M1R  43.750072 -79.295849
12          M1S  43.794200 -79.262029
13          M1T  43.781638 -79.304302
14          M1V  43.815252 -79.284577
15          M1W  43.799525 -79.318389
16          M1X  43.836125 -79.205636
17          M2H  43.803762 -79.363452
18          M2J  43.778517 -79.346556
19          M2K  43.786947 -79.385975
20          M2L  43.757490 -79.374714
21          M2M  43.789053 -79.408493
22          M2N  43.770120 -79.408493
23          M2P  43.752758 -79.400049
24          M2R  43.782736 -79.442259
25          M3A  43.753259 -79.329656
26          M3B  43.745906 -79.352188
27          M3C  43.725900 -79.340923
28          M3H  43.754328 -79.442259
29          M3J  43.767980 -79.487262
30          M3K  43.737473 -79.464763
31          M3L  43.739015 -79.506944
32          M3M  43.728496 -79.495697
33          M3N  43.761631 -79.520999
34          M4A  43.725882 -79.315572
35          M4B  43.706397 -79.309937
36          M4C  43.695344 -79.318389
37          M4E  43.676357 -79.293031
38          M4G  43.709060 -79.363452
39          M4H  43.705369 -79.349372
40          M4J  43.685347 -79.338106
41          M4K  43.679557 -79.352188
42          M4L  43.668999 -79.315572
43          M4M  43.659526 -79.340923
44          M4N  43.728020 -79.388790
45          M4P  43.712751 -79.390197
46          M4R  43.715383 -79.405678
47          M4S  43.704324 -79.388790
48          M4T  43.689574 -79.383160
49          M4V  43.686412 -79.400049
50          M4W  43.679563 -79.377529
51          M4X  43.667967 -79.367675
52          M4Y  43.665860 -79.383160
53          M5A  43.654260 -79.360636
54          M5B  43.657162 -79.378937
55          M5C  43.651494 -79.375418
56          M5E  43.644771 -79.373306
57          M5G  43.657952 -79.387383
58          M5H  43.650571 -79.384568
59          M5J  43.640816 -79.381752
60          M5K  43.647177 -79.381576
61          M5L  43.648198 -79.379817
62          M5M  43.733283 -79.419750
63          M5N  43.711695 -79.416936
64          M5P  43.696948 -79.411307
65          M5R  43.672710 -79.405678
66          M5S  43.662696 -79.400049
67          M5T  43.653206 -79.400049
68          M5V  43.628947 -79.394420
69          M5W  43.646435 -79.374846
70          M5X  43.648429 -79.382280
71          M6A  43.718518 -79.464763
72          M6B  43.709577 -79.445073
73          M6C  43.693781 -79.428191
74          M6E  43.689026 -79.453512
75          M6G  43.669542 -79.422564
76          M6H  43.669005 -79.442259
77          M6J  43.647927 -79.419750
78          M6K  43.636847 -79.428191
79          M6L  43.713756 -79.490074
80          M6M  43.691116 -79.476013
81          M6N  43.673185 -79.487262
82          M6P  43.661608 -79.464763
83          M6R  43.648960 -79.456325
84          M6S  43.651571 -79.484450
85          M7A  43.662301 -79.389494
86          M7R  43.636966 -79.615819
87          M7Y  43.662744 -79.321558
88          M8V  43.605647 -79.501321
89          M8W  43.602414 -79.543484
90          M8X  43.653654 -79.506944
91          M8Y  43.636258 -79.498509
92          M8Z  43.628841 -79.520999
93          M9A  43.667856 -79.532242
94          M9B  43.650943 -79.554724
95          M9C  43.643515 -79.577201
96          M9L  43.756303 -79.565963
97          M9M  43.724766 -79.532242
98          M9N  43.706876 -79.518188
99          M9P  43.696319 -79.532242
100         M9R  43.688905 -79.554724
101         M9V  43.739416 -79.588437
102         M9W  43.706748 -79.594054

## ANSWER TO PART 2 HERE:

In [709]:
df2['Latitude'] = bb['Latitude']
df2['Longitude'] = bb['Longitude']
df2

PostalCode           Borough  \
0          M1B       Scarborough   
1          M1C       Scarborough   
2          M1E       Scarborough   
3          M1G       Scarborough   
4          M1H       Scarborough   
5          M1J       Scarborough   
6          M1K       Scarborough   
7          M1L       Scarborough   
8          M1M       Scarborough   
9          M1N       Scarborough   
10         M1P       Scarborough   
11         M1R       Scarborough   
12         M1S       Scarborough   
13         M1T       Scarborough   
14         M1V       Scarborough   
15         M1W       Scarborough   
16         M1X       Scarborough   
17         M2H        North York   
18         M2J        North York   
19         M2K        North York   
20         M2L        North York   
21         M2M        North York   
22         M2N        North York   
23         M2P        North York   
24         M2R        North York   
25         M3A        North York   
26         M3B        North York   
27         M3C        North York   
28         M3H        North York   
29         M3J        North York   
30         M3K        North York   
31         M3L        North York   
32         M3M        North York   
33         M3N        North York   
34         M4A        North York   
35         M4B         East York   
36         M4C         East York   
37         M4E      East Toronto   
38         M4G         East York   
39         M4H         East York   
40         M4J         East York   
41         M4K      East Toronto   
42         M4L      East Toronto   
43         M4M      East Toronto   
44         M4N   Central Toronto   
45         M4P   Central Toronto   
46         M4R   Central Toronto   
47         M4S   Central Toronto   
48         M4T   Central Toronto   
49         M4V   Central Toronto   
50         M4W  Downtown Toronto   
51         M4X  Downtown Toronto   
52         M4Y  Downtown Toronto   
53         M5A  Downtown Toronto   
54         M5B  Downtown Toronto   
55         M5C  Downtown Toronto   
56         M5E  Downtown Toronto   
57         M5G  Downtown Toronto   
58         M5H  Downtown Toronto   
59         M5J  Downtown Toronto   
60         M5K  Downtown Toronto   
61         M5L  Downtown Toronto   
62         M5M        North York   
63         M5N   Central Toronto   
64         M5P   Central Toronto   
65         M5R   Central Toronto   
66         M5S  Downtown Toronto   
67         M5T  Downtown Toronto   
68         M5V  Downtown Toronto   
69         M5W  Downtown Toronto   
70         M5X  Downtown Toronto   
71         M6A        North York   
72         M6B        North York   
73         M6C              York   
74         M6E              York   
75         M6G  Downtown Toronto   
76         M6H      West Toronto   
77         M6J      West Toronto   
78         M6K      West Toronto   
79         M6L        North York   
80         M6M              York   
81         M6N              York   
82         M6P      West Toronto   
83         M6R      West Toronto   
84         M6S      West Toronto   
85         M7A  Downtown Toronto   
86         M7R       Mississauga   
87         M7Y      East Toronto   
88         M8V         Etobicoke   
89         M8W         Etobicoke   
90         M8X         Etobicoke   
91         M8Y         Etobicoke   
92         M8Z         Etobicoke   
93         M9A      Queen's Park   
94         M9B         Etobicoke   
95         M9C         Etobicoke   
96         M9L        North York   
97         M9M        North York   
98         M9N              York   
99         M9P         Etobicoke   
100        M9R         Etobicoke   
101        M9V         Etobicoke   
102        M9W         Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                       Rouge, Malvern  43.806686 -79.194353  
1               Highland Creek, Rouge Hill, Port Union  43.784535 -79.160497  
2                    G

In [710]:
df2 = df2.set_index('PostalCode')
df2 = df2[['Borough', 'Latitude', 'Longitude', 'Neighborhood']]
df2

Borough   Latitude  Longitude  \
PostalCode                                           
M1B              Scarborough  43.806686 -79.194353   
M1C              Scarborough  43.784535 -79.160497   
M1E              Scarborough  43.763573 -79.188711   
M1G              Scarborough  43.770992 -79.216917   
M1H              Scarborough  43.773136 -79.239476   
M1J              Scarborough  43.744734 -79.239476   
M1K              Scarborough  43.727929 -79.262029   
M1L              Scarborough  43.711112 -79.284577   
M1M              Scarborough  43.716316 -79.239476   
M1N              Scarborough  43.692657 -79.264848   
M1P              Scarborough  43.757410 -79.273304   
M1R              Scarborough  43.750072 -79.295849   
M1S              Scarborough  43.794200 -79.262029   
M1T              Scarborough  43.781638 -79.304302   
M1V              Scarborough  43.815252 -79.284577   
M1W              Scarborough  43.799525 -79.318389   
M1X              Scarborough  43.836125 -79.205636   
M2H               North York  43.803762 -79.363452   
M2J               North York  43.778517 -79.346556   
M2K               North York  43.786947 -79.385975   
M2L               North York  43.757490 -79.374714   
M2M               North York  43.789053 -79.408493   
M2N               North York  43.770120 -79.408493   
M2P               North York  43.752758 -79.400049   
M2R               North York  43.782736 -79.442259   
M3A               North York  43.753259 -79.329656   
M3B               North York  43.745906 -79.352188   
M3C               North York  43.725900 -79.340923   
M3H               North York  43.754328 -79.442259   
M3J               North York  43.767980 -79.487262   
M3K               North York  43.737473 -79.464763   
M3L               North York  43.739015 -79.506944   
M3M               North York  43.728496 -79.495697   
M3N               North York  43.761631 -79.520999   
M4A               North York  43.725882 -79.315572   
M4B                East York  43.706397 -79.309937   
M4C                East York  43.695344 -79.318389   
M4E             East Toronto  43.676357 -79.293031   
M4G                East York  43.709060 -79.363452   
M4H                East York  43.705369 -79.349372   
M4J                East York  43.685347 -79.338106   
M4K             East Toronto  43.679557 -79.352188   
M4L             East Toronto  43.668999 -79.315572   
M4M             East Toronto  43.659526 -79.340923   
M4N          Central Toronto  43.728020 -79.388790   
M4P          Central Toronto  43.712751 -79.390197   
M4R          Central Toronto  43.715383 -79.405678   
M4S          Central Toronto  43.704324 -79.388790   
M4T          Central Toronto  43.689574 -79.383160   
M4V          Central Toronto  43.686412 -79.400049   
M4W         Downtown Toronto  43.679563 -79.377529   
M4X         Downtown Toronto  43.667967 -79.367675   
M4Y         Downtown Toronto  43.665860 -79.383160   
M5A         Downtown Toronto  43.654260 -79.360636   
M5B         Downtown Toronto  43.657162 -79.378937   
M5C         Downtown Toronto  43.651494 -79.375418   
M5E         Downtown Toronto  43.644771 -79.373306   
M5G         Downtown Toronto  43.657952 -79.387383   
M5H         Downtown Toronto  43.650571 -79.384568   
M5J         Downtown Toronto  43.640816 -79.381752   
M5K         Downtown Toronto  43.647177 -79.381576   
M5L         Downtown Toronto  43.648198 -79.379817   
M5M               North York  43.733283 -79.419750   
M5N          Central Toronto  43.711695 -79.416936   
M5P          Central Toronto  43.696948 -79.411307   
M5R          Central Toronto  43.672710 -79.405678   
M5S         Downtown Toronto  43.662696 -79.400049   
M5T         Downtown Toronto  43.653206 -79.400049   
M5V         Downtown Toronto  43.628947 -79.394420   
M5W         Downtown Toronto  43.646435 -79.374846   
M5X         Downtown Toronto  43.648429 -79.382280   
M6A               North York  43.718518 -79.464763   
M6B               North Y

## Now, I will use FourSquare API to search venues near the M5R postal code in Central Toronto, just as a test to see the data before we get down to business!

## Answer to Part 3 (from here until end of notebook):

In [711]:
CLIENT_ID = '2E3HE34ZZO3QIDOW4MKQKDRGFO30NV1AGQE5OBY4ZUABRMRE'
CLIENT_SECRET = 'IJKYWZKEETG2ISNIGVRPNU13XX3K2FHCBGVU3V3Y1O0PB1XG'
VERSION = '20180604'
LIMIT = 50
radius = 600
latitude = df2.loc['M5R', 'Latitude']
longitude = df2.loc['M5R', 'Longitude']

In [712]:
url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, radius, LIMIT)

In [713]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e347fd0c94979001bd36407'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'The Annex',
  'headerFullLocation': 'The Annex, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 33,
  'suggestedBounds': {'ne': {'lat': 43.678109705400004,
    'lng': -79.39822651036465},
   'sw': {'lat': 43.66730969459999, 'lng': -79.41313028963538}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4c62c59ce1621b8dd0332453',
       'name': 'Roti Cuisine of India',
       'location': {'address': '308 Dupont St.',
        'crossStreet': 'at Walmer Rd.',
        'lat': 43.67461834990478,
        'lng': -79.40824866273744,
        'labeledLatLngs'

## Now, to real business. I am going to create a function that will allow me to use FourSquare API to scan multiple neighborhoods for venues and input the data into a dataframe. I will use the function to map the most common venues in each neighborhood of Old Toronto (by postal code)!

In [714]:
LIMIT = 30
def check_venues(names, latitudes, longitudes, radius=500):
    
    venues_list = []
    for name, lat, long in zip(names, latitudes, longitudes):
        print(name)
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION,
            lat,
            long,
            radius,
            LIMIT)
    
        results = requests.get(url).json()["response"]['groups'][0]['items']
        venues_list.append([(
            name, 
            lat, 
            long, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
    
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [628]:
ot_df = df2[df2['Borough'].str.contains('Toronto')].reset_index()
ot_df

PostalCode           Borough   Latitude  Longitude  \
0         M4E      East Toronto  43.676357 -79.293031   
1         M4K      East Toronto  43.679557 -79.352188   
2         M4L      East Toronto  43.668999 -79.315572   
3         M4M      East Toronto  43.659526 -79.340923   
4         M4N   Central Toronto  43.728020 -79.388790   
5         M4P   Central Toronto  43.712751 -79.390197   
6         M4R   Central Toronto  43.715383 -79.405678   
7         M4S   Central Toronto  43.704324 -79.388790   
8         M4T   Central Toronto  43.689574 -79.383160   
9         M4V   Central Toronto  43.686412 -79.400049   
10        M4W  Downtown Toronto  43.679563 -79.377529   
11        M4X  Downtown Toronto  43.667967 -79.367675   
12        M4Y  Downtown Toronto  43.665860 -79.383160   
13        M5A  Downtown Toronto  43.654260 -79.360636   
14        M5B  Downtown Toronto  43.657162 -79.378937   
15        M5C  Downtown Toronto  43.651494 -79.375418   
16        M5E  Downtown Toronto  43.644771 -79.373306   
17        M5G  Downtown Toronto  43.657952 -79.387383   
18        M5H  Downtown Toronto  43.650571 -79.384568   
19        M5J  Downtown Toronto  43.640816 -79.381752   
20        M5K  Downtown Toronto  43.647177 -79.381576   
21        M5L  Downtown Toronto  43.648198 -79.379817   
22        M5N   Central Toronto  43.711695 -79.416936   
23        M5P   Central Toronto  43.696948 -79.411307   
24        M5R   Central Toronto  43.672710 -79.405678   
25        M5S  Downtown Toronto  43.662696 -79.400049   
26        M5T  Downtown Toronto  43.653206 -79.400049   
27        M5V  Downtown Toronto  43.628947 -79.394420   
28        M5W  Downtown Toronto  43.646435 -79.374846   
29        M5X  Downtown Toronto  43.648429 -79.382280   
30        M6G  Downtown Toronto  43.669542 -79.422564   
31        M6H      West Toronto  43.669005 -79.442259   
32        M6J      West Toronto  43.647927 -79.419750   
33        M6K      West Toronto  43.636847 -79.428191   
34        M6P      West Toronto  43.661608 -79.464763   
35        M6R      West Toronto  43.648960 -79.456325   
36        M6S      West Toronto  43.651571 -79.484450   
37        M7A  Downtown Toronto  43.662301 -79.389494   
38        M7Y      East Toronto  43.662744 -79.321558   

                                         Neighborhood  
0                                         The Beaches  
1                        The Danforth West, Riverdale  
2                      The Beaches West, India Bazaar  
3                                     Studio District  
4                                       Lawrence Park  
5                                    Davisville North  
6                                  North Toronto West  
7                                          Davisville  
8                         Moore Park, Summerhill East  
9   Deer Park, Forest Hill SE, Rathnelly, South Hi...  
10                                           Rosedale  
11                        Cabbagetown, St. James Town  
12                               Church and Wellesley  
13                                       Harbourfront  
14                           Ryerson, Garden District  
15                                     St. James Town  
16                                        Berczy Park  
17                                 Central Bay Street  
18                           Adelaide, King, Richmond  
19  Harbourfront East, Toronto Islands, Union Station  
20           Design Exchange, Toronto Dominion Centre  
21                     Commerce Court, Victoria Hotel  
22                                           Roselawn  
23                Forest Hill North, Forest Hill West  
24                The Annex, North Midtown, Yorkville  
25                     Harbord, University of Toronto  
26          Chinatown, Grange Park, Kensington Market  
27  CN Tower, Bathurst Quay, Island airport, Harbo...  
28                    Stn A PO Boxes 25 The Esplanade  
29             First Canadian Place, Under

In [716]:
old_toronto_venues = check_venues(names=ot_df['PostalCode'], latitudes=ot_df['Latitude'], longitudes=ot_df['Longitude'])
old_toronto_venues

M4E
M4K
M4L
M4M
M4N
M4P
M4R
M4S
M4T
M4V
M4W
M4X
M4Y
M5A
M5B
M5C
M5E
M5G
M5H
M5J
M5K
M5L
M5N
M5P
M5R
M5S
M5T
M5V
M5W
M5X
M6G
M6H
M6J
M6K
M6P
M6R
M6S
M7A
M7Y


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0            M4E              43.676357              -79.293031   
1            M4E              43.676357              -79.293031   
2            M4E              43.676357              -79.293031   
3            M4E              43.676357              -79.293031   
4            M4K              43.679557              -79.352188   
5            M4K              43.679557              -79.352188   
6            M4K              43.679557              -79.352188   
7            M4K              43.679557              -79.352188   
8            M4K              43.679557              -79.352188   
9            M4K              43.679557              -79.352188   
10           M4K              43.679557              -79.352188   
11           M4K              43.679557              -79.352188   
12           M4K              43.679557              -79.352188   
13           M4K              43.679557              -79.352188   
14           M4K              43.679557              -79.352188   
15           M4K              43.679557              -79.352188   
16           M4K              43.679557              -79.352188   
17           M4K              43.679557              -79.352188   
18           M4K              43.679557              -79.352188   
19           M4K              43.679557              -79.352188   
20           M4K              43.679557              -79.352188   
21           M4K              43.679557              -79.352188   
22           M4K              43.679557              -79.352188   
23           M4K              43.679557              -79.352188   
24           M4K              43.679557              -79.352188   
25           M4K              43.679557              -79.352188   
26           M4K              43.679557              -79.352188   
27           M4K              43.679557              -79.352188   
28           M4K              43.679557              -79.352188   
29           M4K              43.679557              -79.352188   
30           M4K              43.679557              -79.352188   
31           M4K              43.679557              -79.352188   
32           M4K              43.679557              -79.352188   
33           M4K              43.679557              -79.352188   
34           M4L              43.668999              -79.315572   
35           M4L              43.668999              -79.315572   
36           M4L              43.668999              -79.315572   
37           M4L              43.668999              -79.315572   
38           M4L              43.668999              -79.315572   
39           M4L              43.668999              -79.315572   
40           M4L              43.668999              -79.315572   
41           M4L              43.668999              -79.315572   
42           M4L              43.668999              -79.315572   
43           M4L              43.668999              -79.315572   
44           M4L              43.668999              -79.315572   
45           M4L              43.668999              -79.315572   
46           M4L              43.668999              -79.315572   
47           M4L              43.668999              -79.315572   
48           M4L              43.668999              -79.315572   
49           M4L              43.668999              -79.315572   
50           M4L              43.668999              -79.315572   
51           M4L              43.668999              -79.315572   
52           M4L              43.668999              -79.315572   
53           M4L              43.668999              -79.315572   
54           M4M              43.659526              -79.340923   
55           M4M              43.659526              -79.340923   
56           M4M              43.659526              -79.340923   
57           M4M              43.659526              -79.340923   
58           M4M              43.659526            

In [750]:
old_toronto_cat1 = pd.get_dummies(old_toronto_venues[['Venue Category']], prefix = '', prefix_sep= '')
old_toronto_cat1 = old_toronto_cat1.drop('Neighborhood', axis=1)
old_toronto_cat1.insert(loc=0, column='Neighborhood', value=old_toronto_venues['Neighborhood'],)

old_toronto_cat1

Neighborhood  Airport  Airport Food Court  Airport Gate  Airport Lounge  \
0            M4E        0                   0             0               0   
1            M4E        0                   0             0               0   
2            M4E        0                   0             0               0   
3            M4E        0                   0             0               0   
4            M4K        0                   0             0               0   
5            M4K        0                   0             0               0   
6            M4K        0                   0             0               0   
7            M4K        0                   0             0               0   
8            M4K        0                   0             0               0   
9            M4K        0                   0             0               0   
10           M4K        0                   0             0               0   
11           M4K        0                   0             0               0   
12           M4K        0                   0             0               0   
13           M4K        0                   0             0               0   
14           M4K        0                   0             0               0   
15           M4K        0                   0             0               0   
16           M4K        0                   0             0               0   
17           M4K        0                   0             0               0   
18           M4K        0                   0             0               0   
19           M4K        0                   0             0               0   
20           M4K        0                   0             0               0   
21           M4K        0                   0             0               0   
22           M4K        0                   0             0               0   
23           M4K        0                   0             0               0   
24           M4K        0                   0             0               0   
25           M4K        0                   0             0               0   
26           M4K        0                   0             0               0   
27           M4K        0                   0             0               0   
28           M4K        0                   0             0               0   
29           M4K        0                   0             0               0   
30           M4K        0                   0             0               0   
31           M4K        0                   0             0               0   
32           M4K        0                   0             0               0   
33           M4K        0                   0             0               0   
34           M4L        0                   0             0               0   
35           M4L        0                   0             0               0   
36           M4L        0                   0             0               0   
37           M4L        0                   0             0               0   
38           M4L        0                   0             0               0   
39           M4L        0                   0             0               0   
40           M4L        0                   0             0               0   
41           M4L        0                   0             0               0   
42           M4L        0                   0             0               0   
43           M4L        0                   0             0               0   
44           M4L        0                   0             0               0   
45           M4L        0                   0             0               0   
46           M4L        0                   0             0               0   
47           M4L        0                   0             0               0   
48           M4L        0                   0             0               0   
49           M4L        0                   0         

In [751]:
old_toronto_grouped = old_toronto_cat1.groupby('Neighborhood', axis=0).mean().reset_index()
old_toronto_grouped

Neighborhood   Airport  Airport Food Court  Airport Gate  Airport Lounge  \
0           M4E  0.000000            0.000000      0.000000        0.000000   
1           M4K  0.000000            0.000000      0.000000        0.000000   
2           M4L  0.000000            0.000000      0.000000        0.000000   
3           M4M  0.000000            0.000000      0.000000        0.000000   
4           M4N  0.000000            0.000000      0.000000        0.000000   
5           M4P  0.000000            0.000000      0.000000        0.000000   
6           M4R  0.000000            0.000000      0.000000        0.000000   
7           M4S  0.000000            0.000000      0.000000        0.000000   
8           M4T  0.000000            0.000000      0.000000        0.000000   
9           M4V  0.000000            0.000000      0.000000        0.000000   
10          M4W  0.000000            0.000000      0.000000        0.000000   
11          M4X  0.000000            0.000000      0.000000        0.000000   
12          M4Y  0.000000            0.000000      0.000000        0.000000   
13          M5A  0.000000            0.000000      0.000000        0.000000   
14          M5B  0.000000            0.000000      0.000000        0.000000   
15          M5C  0.000000            0.000000      0.000000        0.000000   
16          M5E  0.000000            0.000000      0.000000        0.000000   
17          M5G  0.000000            0.000000      0.000000        0.000000   
18          M5H  0.000000            0.000000      0.000000        0.000000   
19          M5J  0.000000            0.000000      0.000000        0.000000   
20          M5K  0.000000            0.000000      0.000000        0.000000   
21          M5L  0.000000            0.000000      0.000000        0.000000   
22          M5N  0.000000            0.000000      0.000000        0.000000   
23          M5P  0.000000            0.000000      0.000000        0.000000   
24          M5R  0.000000            0.000000      0.000000        0.000000   
25          M5S  0.000000            0.000000      0.000000        0.000000   
26          M5T  0.000000            0.000000      0.000000        0.000000   
27          M5V  0.055556            0.055556      0.055556        0.111111   
28          M5W  0.000000            0.000000      0.000000        0.000000   
29          M5X  0.000000            0.000000      0.000000        0.000000   
30          M6G  0.000000            0.000000      0.000000        0.000000   
31          M6H  0.000000            0.000000      0.000000        0.000000   
32          M6J  0.000000            0.000000      0.000000        0.000000   
33          M6K  0.000000            0.000000      0.000000        0.000000   
34          M6P  0.000000            0.000000      0.000000        0.000000   
35          M6R  0.000000            0.000000      0.000000        0.000000   
36          M6S  0.000000            0.000000      0.000000        0.000000   
37          M7A  0.000000            0.000000      0.000000        0.000000   
38          M7Y  0.000000            0.000000      0.000000        0.000000   

    Airport Service  Airport Terminal  American Restaurant  Antique Shop  \
0          0.000000          0.000000             0.000000      0.000000   
1          0.000000          0.000000             0.000000      0.000000   
2          0.000000          0.000000             0.000000      0.000000   
3          0.000000          0.000000             0.066667      0.000000   
4          0.000000          0.000000             0.000000      0.000000   
5          0.000000          0.000000             0.000000      0.000000   
6          0.000000          0.000000             0.000000      0.000000   
7          0.000000          0.000000             0.000000      0.000000   
8          0.000000          0.000000             0.000000      0.000000   
9          0.000000          0.000000             0.071429      0.000000   
10    

In [752]:
num_top_venues = 5

for hood in old_toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = old_toronto_grouped[old_toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----M4E----
               venue  freq
0  Health Food Store  0.25
1                Pub  0.25
2              Trail  0.25
3            Airport  0.00
4             Museum  0.00


----M4K----
                venue  freq
0    Greek Restaurant  0.30
1  Italian Restaurant  0.07
2      Ice Cream Shop  0.07
3         Yoga Studio  0.03
4     Bubble Tea Shop  0.03


----M4L----
              venue  freq
0              Park  0.10
1    Sandwich Place  0.10
2               Gym  0.05
3  Sushi Restaurant  0.05
4               Pub  0.05


----M4M----
                 venue  freq
0                 Café  0.13
1          Coffee Shop  0.10
2  American Restaurant  0.07
3   Italian Restaurant  0.07
4               Bakery  0.07


----M4N----
           venue  freq
0           Park  0.33
1       Bus Line  0.33
2    Swim School  0.33
3        Airport  0.00
4  Movie Theater  0.00


----M4P----
               venue  freq
0                Gym  0.14
1     Breakfast Spot  0.14
2               Park  0.14
3  Food & Dr

In [753]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [777]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

columns = ['']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = old_toronto_grouped['Neighborhood']

for ind in np.arange(old_toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:-1] = return_most_common_venues(old_toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0  NaN                 Trail                   Pub     Health Food Store   
1  NaN      Greek Restaurant    Italian Restaurant        Ice Cream Shop   
2  NaN        Sandwich Place                  Park             Pet Store   
3  NaN                  Café           Coffee Shop    Italian Restaurant   
4  NaN                  Park           Swim School              Bus Line   

  4th Most Common Venue 5th Most Common Venue      6th Most Common Venue  \
0           Yoga Studio         Deli / Bodega       Ethiopian Restaurant   
1           Yoga Studio       Bubble Tea Shop                  Juice Bar   
2          Burger Joint         Burrito Place         Italian Restaurant   
3   American Restaurant                Bakery  Middle Eastern Restaurant   
4           Yoga Studio      Department Store          Electronics Store   

         7th Most Common Venue        8th Most Common Venue  \
0            Electronics Store  Eastern European Restaurant   
1                    Bookstore                   Restaurant   
2               Ice Cream Shop                 Liquor Store   
3              Coworking Space      Comfort Food Restaurant   
4  Eastern European Restaurant          Dumpling Restaurant   

  9th Most Common Venue 10th Most Common Venue Neighborhood  
0   Dumpling Restaurant             Donut Shop          M4E  
1                   Spa                  Diner          M4K  
2                   Pub   Fast Food Restaurant          M4L  
3        Ice Cream Shop       Stationery Store          M4M  
4            Donut Shop                Dog Run          M4N

In [778]:
neighborhoods_venues_sorted = neighborhoods_venues_sorted.drop(neighborhoods_venues_sorted.columns[0], axis=1)
cols = list(neighborhoods_venues_sorted)
cols.insert(0, cols.pop(cols.index('Neighborhood')))
neighborhoods_venues_sorted = neighborhoods_venues_sorted.loc[:, cols]
neighborhoods_venues_sorted

Neighborhood 1st Most Common Venue  2nd Most Common Venue  \
0           M4E                 Trail                    Pub   
1           M4K      Greek Restaurant     Italian Restaurant   
2           M4L        Sandwich Place                   Park   
3           M4M                  Café            Coffee Shop   
4           M4N                  Park            Swim School   
5           M4P                 Hotel                   Park   
6           M4R        Clothing Store            Coffee Shop   
7           M4S          Dessert Shop     Italian Restaurant   
8           M4T                   Gym                  Trail   
9           M4V                   Pub            Coffee Shop   
10          M4W                  Park             Playground   
11          M4X           Coffee Shop     Italian Restaurant   
12          M4Y               Gay Bar           Burger Joint   
13          M5A           Coffee Shop                   Park   
14          M5B           Coffee Shop                   Café   
15          M5C            Restaurant                  Hotel   
16          M5E           Coffee Shop         Farmers Market   
17          M5G           Coffee Shop     Italian Restaurant   
18          M5H            Steakhouse       Asian Restaurant   
19          M5J                  Park                  Hotel   
20          M5K           Coffee Shop                   Café   
21          M5L                  Café            Coffee Shop   
22          M5N                  Pool                 Garden   
23          M5P                 Trail       Sushi Restaurant   
24          M5R        Sandwich Place                   Café   
25          M5S                  Café         Sandwich Place   
26          M5T                  Café  Vietnamese Restaurant   
27          M5V       Airport Service         Airport Lounge   
28          M5W          Cocktail Bar                   Café   
29          M5X                  Café            Coffee Shop   
30          M6G         Grocery Store                   Café   
31          M6H                Bakery               Pharmacy   
32          M6J                   Bar       Asian Restaurant   
33          M6K             Nightclub            Coffee Shop   
34          M6P       Thai Restaurant                    Bar   
35          M6R             Gift Shop            Coffee Shop   
36          M6S           Pizza Place                   Café   
37          M7A           Coffee Shop                   Park   
38          M7Y    Light Rail Station            Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue  \
0       Health Food Store           Yoga Studio            Deli / Bodega   
1          Ice Cream Shop           Yoga Studio          Bubble Tea Shop   
2               Pet Store          Burger Joint            Burrito Place   
3      Italian Restaurant   American Restaurant                   Bakery   
4                Bus Line           Yoga Studio         Department Store   
5          Breakfast Spot                   Gym           Sandwich Place   
6     Sporting Goods Shop  Gym / Fitness Center  Health & Beauty Service   
7                     Gym           Pizza Place                     Café   
8             Yoga Studio         Deli / Bodega     Ethiopian Restaurant   
9              Restaurant      Sushi Restaurant             Liquor Store   
10                  Trail           Yoga Studio            Deli / Bodega   
11             Restaurant                  Café                     Park   
12                   Park                   Pub        Indian Restaurant   
13                   Café                   Pub       Mexican Restaurant   
14         Clothing Store         Movie Theater            Burrito Place   
15                   Café           Coffee Shop                Gastropub   
16           Cocktail Bar                  Café                 Beer Bar   
17    Japanese Restaurant                   Spa       Chinese Restaurant  

In [779]:
bb = bb.rename(columns={'Postal Code':'Neighborhood'})
bb
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
df_merged = bb.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

df_merged # check the last columns!

Neighborhood   Latitude  Longitude 1st Most Common Venue  \
0            M1B  43.806686 -79.194353                   NaN   
1            M1C  43.784535 -79.160497                   NaN   
2            M1E  43.763573 -79.188711                   NaN   
3            M1G  43.770992 -79.216917                   NaN   
4            M1H  43.773136 -79.239476                   NaN   
5            M1J  43.744734 -79.239476                   NaN   
6            M1K  43.727929 -79.262029                   NaN   
7            M1L  43.711112 -79.284577                   NaN   
8            M1M  43.716316 -79.239476                   NaN   
9            M1N  43.692657 -79.264848                   NaN   
10           M1P  43.757410 -79.273304                   NaN   
11           M1R  43.750072 -79.295849                   NaN   
12           M1S  43.794200 -79.262029                   NaN   
13           M1T  43.781638 -79.304302                   NaN   
14           M1V  43.815252 -79.284577                   NaN   
15           M1W  43.799525 -79.318389                   NaN   
16           M1X  43.836125 -79.205636                   NaN   
17           M2H  43.803762 -79.363452                   NaN   
18           M2J  43.778517 -79.346556                   NaN   
19           M2K  43.786947 -79.385975                   NaN   
20           M2L  43.757490 -79.374714                   NaN   
21           M2M  43.789053 -79.408493                   NaN   
22           M2N  43.770120 -79.408493                   NaN   
23           M2P  43.752758 -79.400049                   NaN   
24           M2R  43.782736 -79.442259                   NaN   
25           M3A  43.753259 -79.329656                   NaN   
26           M3B  43.745906 -79.352188                   NaN   
27           M3C  43.725900 -79.340923                   NaN   
28           M3H  43.754328 -79.442259                   NaN   
29           M3J  43.767980 -79.487262                   NaN   
30           M3K  43.737473 -79.464763                   NaN   
31           M3L  43.739015 -79.506944                   NaN   
32           M3M  43.728496 -79.495697                   NaN   
33           M3N  43.761631 -79.520999                   NaN   
34           M4A  43.725882 -79.315572                   NaN   
35           M4B  43.706397 -79.309937                   NaN   
36           M4C  43.695344 -79.318389                   NaN   
37           M4E  43.676357 -79.293031                 Trail   
38           M4G  43.709060 -79.363452                   NaN   
39           M4H  43.705369 -79.349372                   NaN   
40           M4J  43.685347 -79.338106                   NaN   
41           M4K  43.679557 -79.352188      Greek Restaurant   
42           M4L  43.668999 -79.315572        Sandwich Place   
43           M4M  43.659526 -79.340923                  Café   
44           M4N  43.728020 -79.388790                  Park   
45           M4P  43.712751 -79.390197                 Hotel   
46           M4R  43.715383 -79.405678        Clothing Store   
47           M4S  43.704324 -79.388790          Dessert Shop   
48           M4T  43.689574 -79.383160                   Gym   
49           M4V  43.686412 -79.400049                   Pub   
50           M4W  43.679563 -79.377529                  Park   
51           M4X  43.667967 -79.367675           Coffee Shop   
52           M4Y  43.665860 -79.383160               Gay Bar   
53           M5A  43.654260 -79.360636           Coffee Shop   
54           M5B  43.657162 -79.378937           Coffee Shop   
55           M5C  43.651494 -79.375418            Restaurant   
56           M5E  43.644771 -79.373306           Coffee Shop   
57           M5G  43.657952 -79.387383           Coffee Shop   
58           M5H  43.650571 -79.384568            Steakhouse   
59           M5J  43.640816 -79.381752                  Park   
60           M5K  43.647177 -79.381576           Coffee Shop   
61           M5L  43.648198 -79.3798

In [780]:
df_merged = df_merged.dropna(axis=0)
df_merged

Neighborhood   Latitude  Longitude 1st Most Common Venue  \
37          M4E  43.676357 -79.293031                 Trail   
41          M4K  43.679557 -79.352188      Greek Restaurant   
42          M4L  43.668999 -79.315572        Sandwich Place   
43          M4M  43.659526 -79.340923                  Café   
44          M4N  43.728020 -79.388790                  Park   
45          M4P  43.712751 -79.390197                 Hotel   
46          M4R  43.715383 -79.405678        Clothing Store   
47          M4S  43.704324 -79.388790          Dessert Shop   
48          M4T  43.689574 -79.383160                   Gym   
49          M4V  43.686412 -79.400049                   Pub   
50          M4W  43.679563 -79.377529                  Park   
51          M4X  43.667967 -79.367675           Coffee Shop   
52          M4Y  43.665860 -79.383160               Gay Bar   
53          M5A  43.654260 -79.360636           Coffee Shop   
54          M5B  43.657162 -79.378937           Coffee Shop   
55          M5C  43.651494 -79.375418            Restaurant   
56          M5E  43.644771 -79.373306           Coffee Shop   
57          M5G  43.657952 -79.387383           Coffee Shop   
58          M5H  43.650571 -79.384568            Steakhouse   
59          M5J  43.640816 -79.381752                  Park   
60          M5K  43.647177 -79.381576           Coffee Shop   
61          M5L  43.648198 -79.379817                  Café   
63          M5N  43.711695 -79.416936                  Pool   
64          M5P  43.696948 -79.411307                 Trail   
65          M5R  43.672710 -79.405678        Sandwich Place   
66          M5S  43.662696 -79.400049                  Café   
67          M5T  43.653206 -79.400049                  Café   
68          M5V  43.628947 -79.394420       Airport Service   
69          M5W  43.646435 -79.374846          Cocktail Bar   
70          M5X  43.648429 -79.382280                  Café   
75          M6G  43.669542 -79.422564         Grocery Store   
76          M6H  43.669005 -79.442259                Bakery   
77          M6J  43.647927 -79.419750                   Bar   
78          M6K  43.636847 -79.428191             Nightclub   
82          M6P  43.661608 -79.464763       Thai Restaurant   
83          M6R  43.648960 -79.456325             Gift Shop   
84          M6S  43.651571 -79.484450           Pizza Place   
85          M7A  43.662301 -79.389494           Coffee Shop   
87          M7Y  43.662744 -79.321558    Light Rail Station   

    2nd Most Common Venue  3rd Most Common Venue 4th Most Common Venue  \
37                    Pub      Health Food Store           Yoga Studio   
41     Italian Restaurant         Ice Cream Shop           Yoga Studio   
42                   Park              Pet Store          Burger Joint   
43            Coffee Shop     Italian Restaurant   American Restaurant   
44            Swim School               Bus Line           Yoga Studio   
45                   Park         Breakfast Spot                   Gym   
46            Coffee Shop    Sporting Goods Shop  Gym / Fitness Center   
47     Italian Restaurant                    Gym           Pizza Place   
48                  Trail            Yoga Studio         Deli / Bodega   
49            Coffee Shop             Restaurant      Sushi Restaurant   
50             Playground                  Trail           Yoga Studio   
51     Italian Restaurant             Restaurant                  Café   
52           Burger Joint                   Park                   Pub   
53                   Park                   Café                   Pub   
54                   Café         Clothing Store         Movie Theater   
55                  Hotel                   Café           Coffee Shop   
56         Farmers Market           Cocktail Bar                  Café   
57     Italian Restaurant    Japanese Restaurant                   Spa   
58       Asian Restaurant                   Café                 Hotel   
59

## Finally, I will use K-means clustering to group the neighborhoods by similarity in terms of venues. Having run the analysis multiple times, I determined that 3 clusters was most appropriate given the data. As you will be able to see, the first cluster of neighborhoods is comprised of mostly restauraunt dominant neighborhoods in central and west-central downtown Toronto, while the second cluster is comprised mainly of recreation oriented neighborhoods closer to North/Midtown Toronto.

In [781]:
kclusters = 3

toronto_group_clust = old_toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_group_clust)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 0, 0, 0, 1, 1, 0, 0, 1, 0], dtype=int32)

In [782]:
df_merged.insert(0,'Cluster Labels', kmeans.labels_)
df_merged

Cluster Labels Neighborhood   Latitude  Longitude 1st Most Common Venue  \
37               1          M4E  43.676357 -79.293031                 Trail   
41               0          M4K  43.679557 -79.352188      Greek Restaurant   
42               0          M4L  43.668999 -79.315572        Sandwich Place   
43               0          M4M  43.659526 -79.340923                  Café   
44               1          M4N  43.728020 -79.388790                  Park   
45               1          M4P  43.712751 -79.390197                 Hotel   
46               0          M4R  43.715383 -79.405678        Clothing Store   
47               0          M4S  43.704324 -79.388790          Dessert Shop   
48               1          M4T  43.689574 -79.383160                   Gym   
49               0          M4V  43.686412 -79.400049                   Pub   
50               1          M4W  43.679563 -79.377529                  Park   
51               0          M4X  43.667967 -79.367675           Coffee Shop   
52               0          M4Y  43.665860 -79.383160               Gay Bar   
53               0          M5A  43.654260 -79.360636           Coffee Shop   
54               0          M5B  43.657162 -79.378937           Coffee Shop   
55               0          M5C  43.651494 -79.375418            Restaurant   
56               0          M5E  43.644771 -79.373306           Coffee Shop   
57               0          M5G  43.657952 -79.387383           Coffee Shop   
58               0          M5H  43.650571 -79.384568            Steakhouse   
59               0          M5J  43.640816 -79.381752                  Park   
60               0          M5K  43.647177 -79.381576           Coffee Shop   
61               0          M5L  43.648198 -79.379817                  Café   
63               2          M5N  43.711695 -79.416936                  Pool   
64               1          M5P  43.696948 -79.411307                 Trail   
65               0          M5R  43.672710 -79.405678        Sandwich Place   
66               0          M5S  43.662696 -79.400049                  Café   
67               0          M5T  43.653206 -79.400049                  Café   
68               0          M5V  43.628947 -79.394420       Airport Service   
69               0          M5W  43.646435 -79.374846          Cocktail Bar   
70               0          M5X  43.648429 -79.382280                  Café   
75               0          M6G  43.669542 -79.422564         Grocery Store   
76               0          M6H  43.669005 -79.442259                Bakery   
77               0          M6J  43.647927 -79.419750                   Bar   
78               0          M6K  43.636847 -79.428191             Nightclub   
82               0          M6P  43.661608 -79.464763       Thai Restaurant   
83               0          M6R  43.648960 -79.456325             Gift Shop   
84               0          M6S  43.651571 -79.484450           Pizza Place   
85               0          M7A  43.662301 -79.389494           Coffee Shop   
87               0          M7Y  43.662744 -79.321558    Light Rail Station   

    2nd Most Common Venue  3rd Most Common Venue 4th Most Common Venue  \
37                    Pub      Health Food Store           Yoga Studio   
41     Italian Restaurant         Ice Cream Shop           Yoga Studio   
42                   Park              Pet Store          Burger Joint   
43            Coffee Shop     Italian Restaurant   American Restaurant   
44            Swim School               Bus Line           Yoga Studio   
45                   Park         Breakfast Spot                   Gym   
46            Coffee Shop    Sporting Goods Shop  Gym / Fitness Center   
47     Italian Restaurant                    Gym           Pizza Place   
48                  Trail            Yoga Studio         Deli / Bodega   
49            Coffee Shop             Restaurant      Sushi Restaurant   
50             Playground    

In [783]:
import matplotlib.cm as cm
import matplotlib.colors as colors


In [784]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(df_merged['Latitude'], df_merged['Longitude'], df_merged['Neighborhood'], df_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow, #[cluster-1]
        fill=True,
        fill_color=rainbow, #[cluster-1]
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [791]:
df_merged.loc[df_merged['Cluster Labels'] == 0, df_merged.columns[list(range(0, df_merged.shape[1]))]]

Cluster Labels Neighborhood   Latitude  Longitude 1st Most Common Venue  \
41               0          M4K  43.679557 -79.352188      Greek Restaurant   
42               0          M4L  43.668999 -79.315572        Sandwich Place   
43               0          M4M  43.659526 -79.340923                  Café   
46               0          M4R  43.715383 -79.405678        Clothing Store   
47               0          M4S  43.704324 -79.388790          Dessert Shop   
49               0          M4V  43.686412 -79.400049                   Pub   
51               0          M4X  43.667967 -79.367675           Coffee Shop   
52               0          M4Y  43.665860 -79.383160               Gay Bar   
53               0          M5A  43.654260 -79.360636           Coffee Shop   
54               0          M5B  43.657162 -79.378937           Coffee Shop   
55               0          M5C  43.651494 -79.375418            Restaurant   
56               0          M5E  43.644771 -79.373306           Coffee Shop   
57               0          M5G  43.657952 -79.387383           Coffee Shop   
58               0          M5H  43.650571 -79.384568            Steakhouse   
59               0          M5J  43.640816 -79.381752                  Park   
60               0          M5K  43.647177 -79.381576           Coffee Shop   
61               0          M5L  43.648198 -79.379817                  Café   
65               0          M5R  43.672710 -79.405678        Sandwich Place   
66               0          M5S  43.662696 -79.400049                  Café   
67               0          M5T  43.653206 -79.400049                  Café   
68               0          M5V  43.628947 -79.394420       Airport Service   
69               0          M5W  43.646435 -79.374846          Cocktail Bar   
70               0          M5X  43.648429 -79.382280                  Café   
75               0          M6G  43.669542 -79.422564         Grocery Store   
76               0          M6H  43.669005 -79.442259                Bakery   
77               0          M6J  43.647927 -79.419750                   Bar   
78               0          M6K  43.636847 -79.428191             Nightclub   
82               0          M6P  43.661608 -79.464763       Thai Restaurant   
83               0          M6R  43.648960 -79.456325             Gift Shop   
84               0          M6S  43.651571 -79.484450           Pizza Place   
85               0          M7A  43.662301 -79.389494           Coffee Shop   
87               0          M7Y  43.662744 -79.321558    Light Rail Station   

    2nd Most Common Venue  3rd Most Common Venue 4th Most Common Venue  \
41     Italian Restaurant         Ice Cream Shop           Yoga Studio   
42                   Park              Pet Store          Burger Joint   
43            Coffee Shop     Italian Restaurant   American Restaurant   
46            Coffee Shop    Sporting Goods Shop  Gym / Fitness Center   
47     Italian Restaurant                    Gym           Pizza Place   
49            Coffee Shop             Restaurant      Sushi Restaurant   
51     Italian Restaurant             Restaurant                  Café   
52           Burger Joint                   Park                   Pub   
53                   Park                   Café                   Pub   
54                   Café         Clothing Store         Movie Theater   
55                  Hotel                   Café           Coffee Shop   
56         Farmers Market           Cocktail Bar                  Café   
57     Italian Restaurant    Japanese Restaurant                   Spa   
58       Asian Restaurant                   Café                 Hotel   
59                  Hotel                  Plaza                  Café   
60                   Café          Deli / Bodega            Restaurant   
61            Coffee Shop          Deli / Bodega   Japanese Restaurant   
65                   Café            Coffee Shop                

In [793]:
df_merged.loc[df_merged['Cluster Labels'] == 1, df_merged.columns[list(range(0, df_merged.shape[1]))]]

Cluster Labels Neighborhood   Latitude  Longitude 1st Most Common Venue  \
37               1          M4E  43.676357 -79.293031                 Trail   
44               1          M4N  43.728020 -79.388790                  Park   
45               1          M4P  43.712751 -79.390197                 Hotel   
48               1          M4T  43.689574 -79.383160                   Gym   
50               1          M4W  43.679563 -79.377529                  Park   
64               1          M5P  43.696948 -79.411307                 Trail   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
37                   Pub     Health Food Store           Yoga Studio   
44           Swim School              Bus Line           Yoga Studio   
45                  Park        Breakfast Spot                   Gym   
48                 Trail           Yoga Studio         Deli / Bodega   
50            Playground                 Trail           Yoga Studio   
64      Sushi Restaurant    Mexican Restaurant         Jewelry Store   

   5th Most Common Venue 6th Most Common Venue        7th Most Common Venue  \
37         Deli / Bodega  Ethiopian Restaurant            Electronics Store   
44      Department Store     Electronics Store  Eastern European Restaurant   
45        Sandwich Place     Food & Drink Shop             Department Store   
48  Ethiopian Restaurant     Electronics Store  Eastern European Restaurant   
50         Deli / Bodega     Electronics Store  Eastern European Restaurant   
64           Yoga Studio          Dessert Shop         Ethiopian Restaurant   

          8th Most Common Venue        9th Most Common Venue  \
37  Eastern European Restaurant          Dumpling Restaurant   
44          Dumpling Restaurant                   Donut Shop   
45                  Yoga Studio  Eastern European Restaurant   
48          Dumpling Restaurant                   Donut Shop   
50          Dumpling Restaurant                   Donut Shop   
64            Electronics Store  Eastern European Restaurant   

   10th Most Common Venue  
37             Donut Shop  
44                Dog Run  
45    Dumpling Restaurant  
48                Dog Run  
50                Dog Run  
64    Dumpling Restaurant

In [794]:
df_merged.loc[df_merged['Cluster Labels'] == 2, df_merged.columns[list(range(0, df_merged.shape[1]))]]

Cluster Labels Neighborhood   Latitude  Longitude 1st Most Common Venue  \
63               2          M5N  43.711695 -79.416936                  Pool   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
63                Garden           Yoga Studio         Deli / Bodega   

   5th Most Common Venue 6th Most Common Venue        7th Most Common Venue  \
63  Ethiopian Restaurant     Electronics Store  Eastern European Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
63   Dumpling Restaurant            Donut Shop                Dog Run